
## Глава 3 Теоремы теории вероятностей

**Кандидат должен знать:**

- Закон больших чисел и усиленный закон больших чисел
- Центральная предельная теорема
- Многомерные распределения

**Материалы:**
- [Райгородский курс по тер. веру лекции 8,9,12,13](https://www.youtube.com/watch?v=n7jx2MfIeX4&list=PLthfp5exSWEr8tRK-Yf-i9aXgcFJ-O16d&index=8)
- [курс ТВ  на степике из частей 2,4](https://stepik.org/course/3089)


## Задачи с кодингом


### 1. Генерация нормальной случайной величины

**Дано:**

Пусть у нас есть случайная величина $\xi \sim U[0,1]$ . 

**Задача:**
1. На основе данной случайной величины с помощью ЦПТ осуществите моделирование  ($n = 10000$) случайной величины  $\eta \sim N(\mu, \sigma^2)$

2. Постройте график полтности распределения и сравните с теоритическим. 

3. Вычислить математического ожидания и дисперсии, сравнить их с истинными значениями.

**Примечания**

1. Для генерации реализаций $\xi$ можно восппользоваться функцией numpy.random.random()
2.  Для построения теоритического графика плотности распределения нормальной величины можно воспользоваться функцией scipy.stats.norm.ppf

### 1. Генерация нормальной случайной величины
### 3. Вычисление мат. ожидания и дисперсии

Let $X$ be a uniformly distributed random variable, and $\eta$ be a normally distributed random variable.

$\eta = \frac{1}{N_x} \sum_{i=1}^{N_x} X_i$
<br>
$\mu_{\eta} = \frac{1}{N_x} \mu \left( \sum_{i=1}^{N_x} X_i \right) = \frac{1}{N_x} \sum_{i=1}^{N} \mu(X_i) = \mu_X$
<br>
$\text{Var}(\eta) = \frac{1}{(N_x-1)^2} \sum_{i=1}^{N_x} \text{Var}(X_i) = \frac{N_x \cdot \text{Var}(X)}{(N_x-1)^2} \approx [\text{if } N_x > 100] \approx \frac{\text{Var}(X)}{N_x}$
<br><br><br>
$\mu_X = \mu_{\eta}$
<br>
$\text{Var}(X) = N_x \cdot \text{Var}(\eta)$


Now I need random uniform values X with mu_x and var_x

In [1]:
import math
import itertools
from tqdm import tqdm

import numpy as np
from scipy.stats import norm

import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go

In [4]:
# eta ~ N(mu, sigma^2)
# X ~ U[a, b]
# Z ~ U[0, 1]

mu_eta = -7
var_eta = 13
sigma_eta = np.sqrt(var_eta)

N_x = 100
mu_x = mu_eta
sigma_x = N_x * var_eta

a = mu_x - np.sqrt(3 * sigma_x)
b = mu_x + np.sqrt(3 * sigma_x)

N_eta = 10**4
Z = np.random.random((N_eta, N_x))
eta = (a + Z * (b - a)).mean(axis=1)


print("###  Task 3: Real E and Var VS Estimated E and Var  ###\n")
      
print(f"Real mu: {mu_eta}; Estimated mu: {eta.mean()}")
print(f"Real var: {var_eta}; Estimated var: {eta.var()}")

###  Task 3: Real E and Var VS Estimated E and Var  ###

Real mu: -7; Estimated mu: -7.0249840176072205
Real var: 13; Estimated var: 12.821324056210727


In [13]:
fig = px.histogram(eta, nbins=40, title="Distribution of eta", labels={"value": "Value"}, height=700, width=500)

In [ ]:
fig.show()

### 2. График полтности распределения. Сравние с теоритическим графиком

In [11]:
fig = go.Figure()

norm_x = np.linspace(norm.ppf(0.0001, loc=mu_eta, scale=sigma_eta), norm.ppf(0.9999, loc=mu_eta, scale=sigma_eta), N_eta)
norm_y = norm.pdf(norm_x, loc=mu_eta, scale=sigma_eta)

fig.add_trace(go.Scatter(x=norm_x, y=norm_y, mode="lines", line=dict(color="darkblue", width=5), name="norm pdf"))

hist_y, hist_x = np.histogram(eta, bins="auto", density=True)
fig.add_trace(go.Bar(x=hist_x, y=hist_y, opacity=0.6, name="histogram", marker=dict(color="darkgreen")))

fig = fig.update_layout(
    title="Normal Distribution",
    xaxis_title="Value",
    yaxis_title="Density",
    template="plotly_dark",
    legend=dict(x=0.8, y=1.0),
    height=700, 
    width=500
)

In [12]:
fig.show()

### 2. Казино 

В казино имеется две игры:

**a. Кубики:**

Игрок платит 4&#36; и бросает два кубика. Если в сумме выпало 8 и более то игрок получает приз равный полученной сумме.

**b. Разгадай код:**

Есть пятизначный код (на каждой позиции стоит цифра от 0 до 9).  Игрок платит 10&#36; и пытается угадать код:
    
    - Если игрок меньше двух позиций то ничего не получает 
    - Если игрок угадал ровно две позиции из 5-ти, то он получает 50
    - Если игроку гадал ровно три позиции из 5-ти, то выигрыш 200
    - Если игроку гадал ровно четыре позиции из 5-ти, то выигрыш 5000
    - Если игрок угадал весь код правильно то выигрыш 100000.
    После каждой попытка код меняется.

**Задача:**

Пусть $\xi ,  \eta $ - случайные величины равные выигрышу(проигрышу) игрока в раунде.
1. Посчитать $E\xi$ и $E\eta$
2. Смоделировать случайные величины $\xi$ и $\eta $
3. Построить графики сходимости среднего выигрыша(проигрыша) игрока к математическому ожиданию.
4. Одинаковая ли скорость сходимости  сл. величины к своему математическому ожиданию. Почему?
4. Какое бы $n$ - количество эеспериментов вы би взяли, для оценки мат. ожидания?




## a. Кубики
### 1); 2)  Расчет мат. ожидания и моделирование случайных величин

In [41]:
win_amounts = np.array([0 if i < 8 else i for i in range(0, 13)]) - 4

possible_dice_values = [i + j for i in range(1, 7) for j in range(1, 7)]
count_values = [possible_dice_values.count(i) for i in range(2, 13)]
probs = list(map(lambda x: x / 36, count_values))

E_xi = sum([prob * value for prob, value in zip(probs, win_amounts[2:])])  # skip 0 and 1 because we can't get this sums from two dices
second_moment = sum([prob * value**2 for prob, value in zip(probs, win_amounts[2:])])
D_xi = second_moment - E_xi**2

print("Value: Probability -", ",  ".join([f"{i + 2}: {count_values[i]}/36" for i in range(11)]))
print("Probs sum:", sum(count_values) / 36)
print("Theoretical E_xi:", round(E_xi, 5))
print("Theoretical D_xi:", round(D_xi, 5))

Value: Probability - 2: 1/36,  3: 2/36,  4: 3/36,  5: 4/36,  6: 5/36,  7: 6/36,  8: 5/36,  9: 4/36,  10: 3/36,  11: 2/36,  12: 1/36
Probs sum: 1.0
Theoretical E_xi: -0.11111
Theoretical D_xi: 21.82099


In [53]:
np.random.seed(48)

# n_samples = 9*10**3
n_samples = 10400
dice_values = np.random.randint(1, 7, 2*n_samples)
dice_sums = dice_values[::2] + dice_values[1::2]
xi_values = win_amounts[dice_sums]

print("Simulated E_xi:", xi_values.mean())

Simulated E_xi: -0.1160576923076923


### 3. Сходимость среднего выигрыша к математическому ожиданию

In [75]:
def plot(values, mean_value):
    cumulative_means = np.cumsum(values) / np.arange(1, len(values) + 1)

    fig = go.Figure()

    fig.add_trace(go.Scatter(
        x=np.arange(1, len(values) + 1),
        y=cumulative_means,
        mode="lines",
        name="Среднее значение выигрыша"
    ))

    fig.add_trace(go.Scatter(
        x=[1, len(values)],
        y=[mean_value, mean_value],
        mode="lines",
        line=dict(dash="dash", color="red"),
        name="Математическое ожидание"
    ))

    fig.update_layout(
        title="Сходимость среднего выигрыша к математическому ожиданию",
        xaxis_title="Количество наблюдений",
        yaxis_title="Средний выигрыш",
        legend=dict(x=0.8, y=1.0),
        template="plotly_dark"
    )

    fig.show()

In [45]:
plot(xi_values, E_xi)

### **5) Choose N to estimate E**

In [54]:
z = 1.96
eps = 0.09
sigma = np.sqrt(D_xi)

n = ((z * sigma) / eps) ** 2
n

10349.074836153028

## b. Разгадай код
### 1); 2)  Расчет мат. ожидания и моделирование случайных величин

In [57]:
p = 0.1
q = 0.9
guess_code_win_amounts = np.array([0, 0, 50, 200, 5000, 100000]) - 10
code_game_probs = [math.comb(5, i) * p ** i * q ** (5 - i) for i in range(6)]
E_eta = sum([prob * value for prob, value in zip(code_game_probs, guess_code_win_amounts)])
eta_second_moment = sum([prob * value**2 for prob, value in zip(code_game_probs, guess_code_win_amounts)])
D_eta = eta_second_moment - E_eta**2

print("Probs", list(map(lambda x: round(x, 5), code_game_probs)))
print("Probs sum", sum(code_game_probs))
print("Theoretical E_eta:", round(E_eta, 5))
print("Theoretical D_eta:", round(D_eta, 5))

Probs [0.59049, 0.32805, 0.0729, 0.0081, 0.00045, 1e-05]
Probs sum 1.0
Theoretical E_eta: -1.485
Theoretical D_eta: 111683.74478


In [77]:
np.random.seed(111)
N_plays = 1 * 10 ** 1
# N_plays = 10

zeros_code = np.array([0, 0, 0, 0, 0])
arrange_code = np.array([1, 2, 3, 4, 5])
random_values_code = np.random.randint(0, 10, (N_plays, 5))

code_guesses = np.random.randint(0, 10, (N_plays, 5))

is_guess_zeros_code = code_guesses[:] == zeros_code
zeros_guesses = is_guess_zeros_code.sum(axis=1)
zeros_guesses_win_amounts = guess_code_win_amounts[zeros_guesses]
print("zeros E", zeros_guesses_win_amounts.mean())

is_guess_arrange_code = code_guesses[:] == arrange_code
arrange_guesses = is_guess_arrange_code.sum(axis=1)
arrange_guesses_win_amounts = guess_code_win_amounts[arrange_guesses]
print("arrange E", arrange_guesses_win_amounts.mean())

is_guess_random_code = code_guesses == random_values_code
random_guesses = is_guess_random_code.sum(axis=1)
random_guesses_win_amounts = guess_code_win_amounts[random_guesses]
print("random E", random_guesses_win_amounts.mean())

print("real E", round(E_eta, 5))

zeros E -5.0
arrange E -5.0
random E -10.0
real E -1.485


### 3. Сходимость среднего выигрыша к математическому ожиданию

In [76]:
plot(random_guesses_win_amounts[::1000], E_eta)

### Случайный граф


**Условие**

Пусть G(n,p) -  случайный граф на $n$ вершинах, где $p$ - это вероятность появления ребра между любыми двумя вершинами.

Обозначим за $\xi(n,p)$ - количество треугольников (т.е. полных подграфов на трёх вершинах) в случайном графе  

**Задача 1:**

1. Найти $E\xi$
2. Реализовать моделирование случайного случайного графа и функцию нахождения количества треугольников. 
3. Рассмотрим G(3,p) - случайный граф на трёх вершинах. Реализуйте $\tau$ - случайная величина равная 1 если граф полный и 0 иначе.


**Задача 2:**

- Пусть M(k) - среднее количество треугольников после k генераций случайного графа. 
- И пусть T(k)  - среднее количество треугольников после генераций случайного графа на трёх вершинах (т.е. на каждой итерации генерируем $C_n^3$ графов на трёх вершинах).

1. Верно ли что $M(k) \rightarrow E\xi$ при $k \rightarrow \infty$ 
2. Верно ли что $T(k) \rightarrow  E\xi$ при $k \rightarrow \infty$

3. Рассмотрите два графа $G_1(10, \frac{1}{2})$ и $G_2(10, \frac{1}{20})$.  Построите графики  $M(k)$, $T(k)$ и $E\xi$ (константа) для заданных графов.

**Задача 3**:

Проделайте аналогичные рассуждения для $D \xi$ т.е.
- Найдите  $D \xi$  математически.
- Посчитайте дисперсию количества треугольников, k раз реализуя случайный граф.
- Посчитайте дисперсию количества треугольников, k раз генерируя  $C_n^3$ реализаций случайной величины $\tau$ .
- оцените сходимость
- Постройте графики для графов  $G_1(10, \frac{1}{2})$ и $G_2(10, \frac{1}{20})$.

In [2]:
def generate_graph(n_graphs, n_nodes, edge_p):
    graphs = np.zeros((n_graphs, n_nodes, n_nodes))
    
    n_edges = math.comb(n_nodes, 2)
    is_edge = np.random.random((n_graphs, n_edges)) < edge_p
    node_pairs = list(itertools.combinations([i for i in range(n_nodes)], 2))
    
    for i in range(n_graphs):
        for edge, node_pair in zip(is_edge[i], node_pairs):
            if edge:
                graphs[i][node_pair[0], node_pair[1]] = 1
                graphs[i][node_pair[1], node_pair[0]] = 1
    return graphs


def count_triangles(graphs, possible_loops):
    triangles = []
    for graph in graphs:
        n_triangles = 0
        for node_0, node_1, node_2 in possible_loops:
            if graph[node_0, node_1] and graph[node_0, node_2] and graph[node_1, node_2]:
                n_triangles += 1
        triangles.append(n_triangles)
    return triangles

In [57]:
def generate_graph_optimized(n_graphs, n_nodes, edge_p):
    dtype = np.int8 if n_nodes < 128 else np.int16
    random_values = (np.random.random((n_graphs, n_nodes, n_nodes)) < edge_p).astype(dtype)
    adjacency_matrices = np.triu(random_values, k=1)
    return adjacency_matrices

def count_triangles_optimized(graphs):
    squared_matrix = np.matmul(graphs, graphs)
    triangles_matrix = graphs * squared_matrix
    n_triangles = np.sum(np.triu(triangles_matrix, k=1), axis=(1, 2))
    return n_triangles

In [63]:
%%time
random_graphs = generate_graph_optimized(10**5, 30, 0.05)
triangles = count_triangles_optimized(random_graphs)

print("mean triangles", np.mean(triangles))

mean triangles 0.5091
CPU times: user 2.89 s, sys: 80.1 ms, total: 2.97 s
Wall time: 2.98 s


In [5]:
m_ = m[1]
n = m_.shape[0]
n_riangls = 0
for row in range(n):
    positions = np.where(m_[row] == 1)[0]
    for pos in positions:
        n_riangls += (m_[row] + m_[pos] == 2).sum()

n_riangls

NameError: name 'm' is not defined

### Task 2 
### M(k)

In [13]:
k = 10**5
n = 100
p = 0.05

M_k_loops = list(itertools.combinations([i for i in range(n)], 3))

In [14]:
%%time
random_graphs = generate_graph(k, n, p)

CPU times: user 33.4 s, sys: 2.46 s, total: 35.9 s
Wall time: 35.9 s


In [15]:
%%time
n_triangles_in_each_graph = count_triangles(random_graphs, M_k_loops)

KeyboardInterrupt: 

In [197]:
M_k = np.mean(n_triangles_in_each_graph)
M_k_var = np.var(n_triangles_in_each_graph)

print("M_k:", M_k)
print("var:", M_k_var)

M_k: 15.0072
var: 52.49928816


### T(k)

In [198]:
random_graphs = (np.random.random((k, math.comb(n, 3))) < p**3).astype(int)
N_triangles = random_graphs.sum(axis=1)   

In [199]:
T_k = np.mean(N_triangles)
T_k_var = np.var(N_triangles)

print("T_k:", T_k)
print("var:", T_k_var)

T_k: 14.9918
var: 13.146972760000002


In [200]:
# M_k and T_k mean
math.comb(n, 3)*0.5**3

15.0

In [202]:
# T_k var
math.comb(n, 3)*(0.5**3 - 0.5**6)

13.125